# PEER GROUPS
## Gensim 
Heavily inspired by [machinelearningplus.com](www.

### Imports

In [1]:
import pandas as pd
import numpy as np

from gensim.parsing.preprocessing import remove_stopwords
from gensim import corpora
from gensim import models
from gensim.utils import simple_preprocess
from gensim import similarities
from gensim.parsing.porter import PorterStemmer

import pyLDAvis
import pyLDAvis.gensim

import warnings
warnings.filterwarnings('ignore')

### Intiailize Raw Conference Call Data

#### Read Data

In [2]:
# get list of quarterly calls (events) generated from download_transcripts.py
calls_raw = pd.read_csv('../extracts/foolcalls_extract_20200814.csv')

#### Filter Data

In [ ]:
# only calls from 2019
calls_raw = calls_raw.loc[calls_raw['fiscal_period_year'] == 2019, ]

# remove statement_types that are either unknown or operator (i.e. keeping P, Q, A)
calls_raw = calls_raw.loc[calls_raw['statement_type'].isin(['P'])]

#### Clean & Structure

In [37]:
# remove rows with missing text (nan)
calls_raw = calls_raw.dropna(subset=['text'])

# join text by ticker (i.e. combine individual statements from the same call and combine calls from quarters/years)
calls = calls_raw.loc[:, ['ticker','text']].groupby(['ticker'])['text'].apply(lambda x: ''.join(x)).reset_index()

# assign one company name per ticker because they aren't consistent (e.g. Apple Inc vs Apple, Inc)
ticker_map = calls_raw[['ticker','company_name']].groupby('ticker').head(1)

# merge back to final data frame
calls = calls.merge(ticker_map,on='ticker',how='inner')
calls['ticker_name'] = calls['ticker'] + ': ' + calls['company_name']

## Pre-Processing

In [34]:
# tokenize and remove punctuation
calls['text'] = calls['text'].apply(lambda x: simple_preprocess(x, min_len=2, max_len=15, deacc=True))

# Build the bigram model
bigram = models.Phrases(calls['text'], min_count=5, threshold=50) # higher threshold fewer phrases.
bigram_model = models.phrases.Phraser(bigram)
calls['text'] = calls['text'].apply(lambda x: bigram_model[x])

# remove stopwords
calls['text'] = calls['text'].apply(lambda x: [remove_stopwords(w) for w in x])

# stemming (porter)
p = PorterStemmer()
calls['text'] = calls['text'].apply(lambda x: p.stem_documents(x))

# create dictionary object
dictionary = corpora.Dictionary(calls['text'])

# filter extremes
dictionary.filter_extremes(no_below=5, no_above=0.20)

# bag-of-words transformation
corpus = [dictionary.doc2bow(text) for text in calls['text']]

# tfidf transformation
tfidf = models.TfidfModel(corpus)  # fit model
corpus_tfidf = tfidf[corpus]  # apply model


## LSI Model Transformation

In [35]:
# lsi transformation
lsi_model = models.LsiModel(corpus_tfidf, id2word=dictionary, num_topics=100)  # initialize an LSI transformation
corpus_lsi = lsi_model[corpus_tfidf]  # apply model
for t in lsi_model.show_topics(): # print topics
    print(t)

(0, '0.646*"deposit" + 0.143*"mortgag" + 0.124*"charge_off" + 0.121*"rmb" + 0.111*"lend" + 0.105*"interest_bear" + 0.090*"branch" + 0.087*"merger" + 0.075*"cloud" + 0.072*"nim"')
(1, '-0.510*"deposit" + 0.484*"rmb" + 0.112*"cloud" + 0.110*"clinic" + -0.097*"charge_off" + 0.093*"constant_curr" + 0.086*"noi" + -0.084*"interest_bear" + 0.080*"subscript" + 0.075*"barrel"')
(2, '-0.820*"rmb" + -0.196*"deposit" + -0.115*"foreign_speech" + 0.093*"clinic" + 0.089*"noi" + 0.081*"barrel" + 0.074*"oil" + 0.073*"ffo" + 0.070*"tenant" + 0.069*"rent"')
(3, '0.337*"noi" + -0.307*"clinic" + 0.256*"ffo" + 0.246*"tenant" + 0.240*"square_feet" + 0.235*"rent" + -0.195*"trial" + 0.169*"occup" + -0.148*"therapi" + -0.136*"diseas"')
(4, '-0.310*"barrel" + -0.256*"well" + -0.254*"oil" + -0.243*"drill" + 0.226*"noi" + 0.203*"clinic" + -0.182*"rig" + 0.166*"tenant" + 0.165*"ffo" + 0.160*"square_feet"')
(5, '-0.352*"cloud" + -0.239*"subscript" + 0.213*"clinic" + 0.212*"barrel" + 0.181*"well" + -0.172*"constant_c

## Document Similarities (LSI)

In [71]:
# cosine similarity matrix with lsi
index_lsi = similarities.MatrixSimilarity(corpus_lsi)
sims_lsi = index_lsi[corpus_lsi]

# get top 10 peers for each ticker
n = len(sims_lsi)
for i, s in enumerate(sims_lsi):
    print(calls['ticker_name'].iloc[i])
    print(calls['ticker_name'].iloc[s.argsort()[::-1][:n][1:10]])

# get top peers for each ticker
peers_lsi = pd.DataFrame()
for i, s in enumerate(sims_lsi):
    peers_idx = np.where(s > 0.70)[0].tolist()
    this_df = pd.DataFrame({'company': [calls['ticker_name'].iloc[i]]*len(peers_idx),
                            'peer': calls['ticker_name'].iloc[peers_idx],
                            'value': s[peers_idx]})
    peers_lsi = pd.concat([peers_lsi, this_df])

A: Agilent Technologies
2739        TMO: Thermo Fisher Scientific Inc
2269                          QGEN: Qiagen NV
2523    SMMN.Y: Siemens Healthineers AG (ADR)
2690                    TECH: Bio-Techne Corp
1654                      LMNX: Luminex Corp 
2074               OSUR: OraSure Technologies
2237                   PSNL: Personalis, Inc.
1965            NSTG: Nanostring Technologies
2931                VIVO: Meridian Bioscience
Name: ticker_name, dtype: object
AA: ALCOA CORP
2340                      RIO: Rio Tinto plc
538                   CENX: Century Aluminum
1255                     GSM: Ferroglobe PLC
2380      RS: Reliance Steel And Aluminum Co
2401                    RYI: Ryerson Holding
2434    SCHN: Schnitzer Steel Industries Inc
2900                         VALE: Vale S.A.
613           CMC: Commercial Metals Company
1912               NEXA: Nexa Resources S.A.
Name: ticker_name, dtype: object
AAL: American Airlines Group
116                     ALGT: Allegiant Travel


Name: ticker_name, dtype: object
ATO: Atmos Energy
2500     SJI: South Jersey Industries Inc
2029                     OGS: ONE Gas Inc
2573                       SR: Spire Inc.
2675                TCP: TC Pipelines L P
2639    SWX: Southwest Gas Holdings, Inc.
873                    DTE: DTE Energy Co
678        CPK: Chesapeake Utilities Corp
2776         TRP: TransCanada Corporation
2893                     UTL: Unitil Corp
Name: ticker_name, dtype: object
ATR: Aptargroup Inc
1658                   LNDC: Landec Corp
1519          JJSF: J&J Snack Foods Corp
2137                    PEP: PepsiCo Inc
536         CELH: Celsius Holdings, Inc.
2603                   STKL: SunOpta Inc
511              CCK: Crown Holdings Inc
2514           SLGN: Silgan Holdings Inc
1079                      FLOW: SPX FLOW
1040    FDP: Fresh Del Monte Produce Inc
Name: ticker_name, dtype: object
ATRA: Atara Biotherapeutics, Inc.
599                       CLLS: Cellectis SA
497     CBMG: Cellular Biomedicine Gr

2870                              UNIT: Uniti Group Inc.
3109                       ZAYO: Zayo Group Holdings Inc
732                                 CTL: CenturyLink Inc
2418                       SBAC: SBA Communications Corp
161                             AMT: American Tower Corp
641     CNSL: Consolidated Communications Holdings, Inc.
492                                 CBB: Cincinnati Bell
55                                      ADTN: Adtran Inc
595                                     CLFD: Clearfield
Name: ticker_name, dtype: object
CCJ: Cameco Corp
2691              TECK: Teck Resources Limited
1669    LORL: Loral Space & Communications Inc
1138                         FTS: Fortis, Inc.
826                        DHXM: DHX Media Ltd
2679      TCS: The Container Store Group, Inc.
2655                       TAC: TransAlta Corp
1852                    MTL: Mullen Group Ltd.
1183                            GIB: CGI, Inc.
648         CODI: Compass Diversified Holdings
Name: ticker_n

Name: ticker_name, dtype: object
CWT: California Water Service Group
281         AWR: American States Water Co
280             AWK: American Water Works
2503                        SJW: SJW Corp
2119                PCYO: Pure Cycle Corp
769     CWCO: Consolidated Water Co. Ltd.
967                 ERII: Energy Recovery
2220                      PRMW: Cott Corp
179                   AOS: AO Smith Corp.
3052               WTRG: Aqua America Inc
Name: ticker_name, dtype: object
CX: CEMEX, S.A.B. de C.V.
2621                            SUM: Summit Materials Inc
1010                             EXP: Eagle Materials Inc
1790                   MLM: Martin Marietta Materials Inc
1667    LOMA: Loma Negra Compañía Industrial Argentina...
1031             FBM: Foundation Building Materials, Inc.
2936                VMC: Vulcan Materials Co (Holding Co)
2884                                USCR: US Concrete Inc
1926                      NINE: Nine Energy Service, Inc.
851                          D

1763               MGA: Magna International
292        AXTA: Axalta Coating Systems Ltd
2111                  PBI: Pitney Bowes Inc
3007                         WHR: Whirlpool
1625    LECO: Lincoln Electric Holdings Inc
2012                  OC: Owens Corning Inc
1206                  GM: General Motors Co
929                EMN: Eastman Chemical Co
632               CNHI: CNH Industrial N.V.
Name: ticker_name, dtype: object
FAF: First American Financial Corp
1093       FNF: Fidelity National Financial Inc
2065       ORI: Old Republic International Corp
2597    STC: Stewart Information Services Corp.
1203                       GLUU: Glu Mobile Inc
2344                RLGY: Realogy Holdings Corp
2811    TTWO: Take-Two Interactive Software Inc
1252             GSHD: Goosehead Insurance, Inc
2300                   RDFN: Redfin Corporation
2348                  RMAX: RE/MAX Holdings Inc
Name: ticker_name, dtype: object
FANG: Diamondback Energy Inc
564        CHK: Chesapeake Energy Corp
225

...

Name: ticker_name, dtype: object
OIS: Oil States International Inc
2510                             SLB: Schlumberger NV
1946                  NOV: National Oilwell Varco Inc
1048               FET: Forum Energy Technologies Inc
1904    NESR: National Energy Services Reunited Corp.
2447                           SDRL: Seadrill Limited
196                           APY: Apergy Corporation
846                DO:  Diamond Offshore Drilling Inc
2090                      PACD: PACIFIC DRILLING S.A.
2337                              RIG: Transocean Ltd
Name: ticker_name, dtype: object
OKE: ONEOK Inc (New)
980                   ET: Energy Transfer LP
950     EPD: Enterprise Products Partners LP
201         AR: Antero Resources Corporation
129            ALTM: Altus Midstream Company
2766              TRGP: Targa Resources Corp
932       ENBL: Enable Midstream Partners LP
934               ENLC: EnLink Midstream LLC
858                   DPM: DCP Midstream, LP
540       CEQP: Crestwood Equity 

RCII: Rent-A-Center
58                                     ADYY.F: Adyen N.V.
1254                                 GSKY: GreenSky, Inc.
2480                                    SHOP: Shopify Inc
1247                                        GRPN: Groupon
2258                            PYPL: PayPal Holdings Inc
2799                       TSS: Total System Services Inc
997                              EVOP: EVO Payments, Inc.
1064    FIS: Fidelity National Information Services, Inc.
34                                ACIW: ACI Worldwide Inc
Name: ticker_name, dtype: object
RCKY: Rocky Brands Inc
3000                  WEYS: Weyco Group Inc
657               COLM: Columbia Sportswear
2479                SHOO: Steven Madden Ltd
2835            UA: Under Armour (C Shares)
810              DECK: Deckers Outdoor Corp
682     CPRI: Michael Kors Holdings Limited
2836           UAA: Under Armour (A Shares)
2506                  SKX: Skechers USA Inc
2223          PRPL: Purple Innovation, Inc.
Name: 

987                      ETSY: Etsy Inc
1147    FVRR: Fiverr International Ltd.
890                      EBAY: eBay Inc
1679           LQDT: Liquidity Services
898                ECOM: ChannelAdvisor
1133             FTCH: Farfetch Limited
2388          RUBI: The Rubicon Project
2309                  REAL: TheRealReal
1523        JMIA: JUMIA TECHNOLOGIES AG
Name: ticker_name, dtype: object
SQM: Sociedad Química y Minera de Chile S.A.
107                        ALB: Albemarle Corp
861                       DQ: Daqo New Energy 
1688                        LTHM: Livent Corp.
2451          SEDG: SolarEdge Technologies Inc
717                   CSIQ: Canadian Solar Inc
1125                     FSLR: First Solar Inc
2390                               RUN: Sunrun
1255                       GSM: Ferroglobe PLC
309     BAM: Brookfield Asset Management, Inc.
Name: ticker_name, dtype: object
SQNS: Sequans Communications
2634           SWIR: Sierra Wireless Inc
1250                    GSAT: Global

1725                                     MBI: MBIA
1001                             EVTC: Evertec Inc
82             AGO: Assured Guaranty Ltd (Bermuda)
418                              BPOP: Popular Inc
2545    SOI: Solaris Oilfield Infrastructure, Inc.
139                AMBC: Ambac Financial Group Inc
2588                       SSTI: ShotSpotter, Inc.
1301                    HCLP: Hi-Crush Partners LP
1342              HMTV: Hemisphere Media Group Inc
Name: ticker_name, dtype: object
TV: Grupo Televisa, S.A.B
616                         CMCS.A: Comcast Corp
256                             ATUS: Altice USA
2654                                 T: AT&T Inc
1616                  LBTY.K: Liberty Global PLC
2887     USM: United States Cellular Corporation
2685         TDS: Telephone And Data Systems Inc
573             CHTR: Charter Communications Inc
460                          CABO: Cable One Inc
1137    FTR: Frontier Communications Corporation
Name: ticker_name, dtype: object
TW: Trad

1318     HGV: Hilton Grand Vacations Inc.
2899    VAC: Marriott Vacations Worldwide
2369                         RP: RealPage
1854              MTN: Vail Resorts, Inc.
1446                     INGN: Inogen Inc
1771              MGRC: McGrath Rent Corp
2594                      STAR: iStar Inc
3004                    WHD: Cactus, Inc.
1779                MINI: Mobile Mini Inc
Name: ticker_name, dtype: object
WYNN: Wynn Resorts Ltd
2787      TRWH: Twin River Worldwide Holdings, Inc.
1161                     GDEN: Golden Entertainment
787                      CZR: Caesars Entertainment
1767                 MGM: MGM Resorts International
1696                      LVS: LAS VEGAS SANDS CORP
1820    MPEL: Melco Resorts & Entertainment Limited
2378                        RRR: Red Rock Resources
643                       CNTY: Century Casinos Inc
453                                BYD: Boyd Gaming
Name: ticker_name, dtype: object
X: United States Steel Corp
1978                                 

In [72]:
peers_lsi = peers_lsi.dropna()
peers_lsi.loc[peers_lsi.company.str.contains('NKE'),]

company                                 peer     value
470   NKE: Nike, Inc.                     CAL: Caleres Inc  0.772496
589   NKE: Nike, Inc.             CLAR: Clarus Corporation  0.804264
657   NKE: Nike, Inc.            COLM: Columbia Sportswear  0.819076
682   NKE: Nike, Inc.  CPRI: Michael Kors Holdings Limited  0.860065
697   NKE: Nike, Inc.                    CRI: Carter's Inc  0.777130
704   NKE: Nike, Inc.                          CROX: Crocs  0.843526
810   NKE: Nike, Inc.           DECK: Deckers Outdoor Corp  0.799644
834   NKE: Nike, Inc.       DKS: Dick's Sporting Goods Inc  0.762485
1072  NKE: Nike, Inc.                  FL: Foot Locker Inc  0.871962
1157  NKE: Nike, Inc.                     GCO: Genesco Inc  0.775021
1184  NKE: Nike, Inc.            GIII: G-III Apparel Group  0.836259
1322  NKE: Nike, Inc.                 HIBB: Hibbett Sports  0.724242
1469  NKE: Nike, Inc.              IPAR: Inter Parfums Inc  0.723121
1591  NKE: Nike, Inc.                     KSS: Kohl's Corp  0.757654
1817  NKE: Nike, Inc.                    MOV: Movado Group  0.835660
1930  NKE: Nike, Inc.                      NKE: Nike, Inc.  1.000000
2479  NKE: Nike, Inc.              SHOO: Steven Madden Ltd  0.860730
2506  NKE: Nike, Inc.                SKX: Skechers USA Inc  0.803623
2757  NKE: Nike, Inc.                  TPR: Tapestry, Inc.  0.714760
2835  NKE: Nike, Inc.          UA: Under Armour (C Shares)  0.826871
2836  NKE: Nike, Inc.         UAA: Under Armour (A Shares)  0.851416
2917  NKE: Nike, Inc.                              VFC: VF  0.705428
3000  NKE: Nike, Inc.                WEYS: Weyco Group Inc  0.776851
3062  NKE: Nike, Inc.            WWW: Wolverine World Wide  0.714216
3125  NKE: Nike, Inc.                     ZUMZ: Zumiez Inc  0.776297

#### Export to Cytoscape

In [74]:
peers_lsi.to_csv('output/peers_lsi.csv',sep='|',index=False)

## Lda Model Transformation

In [ ]:
# lda transformation
lda = models.ldamodel.LdaModel(corpus=corpus, id2word=dictionary, num_topics=20)
corpus_lda = lda[corpus] # apply lda model to corpus
lda.print_topics()

# data visualization
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda, corpus, dictionary)
vis

## Document Similarities (LDA)

In [17]:
# cosine similarity matrix with lda
index_lda = similarities.MatrixSimilarity(corpus_lda)
sims_lda = index_lda[corpus_lda]

# get top 10 peers for each ticker
n = len(sims_lda)
for i, s in enumerate(sims_lda):
    print(calls['ticker_name'].iloc[i])
    print(calls['ticker_name'].iloc[s.argsort()[::-1][:n][0:10]])

# get top peers for each ticker
peers_lda = pd.DataFrame()
for i, s in enumerate(sims_lda):
    peers_idx = np.where(s > 0.95)[0].tolist()
    this_df = pd.DataFrame({'company': [calls['ticker_name'].iloc[i]]*len(peers_idx),
                            'peer': calls['ticker_name'].iloc[peers_idx],
                            'value': s[peers_idx]})
    peers_lda = pd.concat([peers_lda, this_df])

A: Agilent Technologies
0                A: Agilent Technologies
1            A: Agilent Technologies Inc
664          CDXC: ChromaDex Corporation
902           CSV: Carriage Services Inc
1828           IVC: Invacare Corporation
2703       PRAH: PRA Health Sciences Inc
2704    PRAH: PRA Health Sciences, Inc. 
3573       VIVO: Meridian Bioscience Inc
2705     PRAH: PRA Health Services, Inc.
922                   CTSO: Cytosorbents
Name: ticker_name, dtype: object
A: Agilent Technologies Inc
1              A: Agilent Technologies Inc
0                  A: Agilent Technologies
664            CDXC: ChromaDex Corporation
79      AEO: American Eagle Outfitters Inc
902             CSV: Carriage Services Inc
865                      CRI: Carter's Inc
409                          BC: Brunswick
1229                EVER: EverQuote, Inc. 
2097                           MAT: Mattel
2807                RCKY: Rocky Brands Inc
Name: ticker_name, dtype: object
AA: ALCOA CORP
2                        AA

Name: ticker_name, dtype: object
APTS: Preferred Apartment Communities, Inc.
2633                   PGRE: Paramount Group
2634               PGRE: Paramount Group Inc
1679    HTA: Healthcare Trust of America Inc
1179                EQC: Equity Commonwealth
72                      ADUS: Addus HomeCare
696     CHCT: Community Healthcare Trust Inc
1002                 DEI: Douglas Emmett Inc
3270                        TCRD: THL Credit
3022                       SHOP: Shopify Inc
2348      NHI: National Health Investors Inc
Name: ticker_name, dtype: object
APTV: Aptiv PLC
242                           APTV: Aptiv PLC
996                      DDD: 3D Systems Corp
3159    ST: Sensata Technologies Holding N.V.
850                        CPS: CPL Resources
851        CPS: Cooper-Standard Holdings Inc.
3750                       XONE: The ExOne Co
3220    SWM: Schweitzer-Mauduit International
1888                          KEM: Kemet Corp
1984                     LFUS: Littelfuse Inc
379       

485     BLDP: Ballard Power Systems Inc
145                     ALE: ALLETE Inc
146                     ALE: Allete Inc
667            CECE: CECO Environmental
86             AES: The AES Corporation
1394                    FTS: Fortis Inc
1354          FOR: Forestar Group, Inc.
2593              PCYO: Pure Cycle Corp
260               ARE: Aecon Group Inc.
651     CCS: Clarity Commerce Solutions
Name: ticker_name, dtype: object
BLDR: Builders Firstsource Inc
486     BLDR: Builders Firstsource Inc
177              AMBA: Ambarella, Inc.
2671            PLOW: Douglas Dynamics
3756                        XRX: Xerox
3354            TOL: Toll Brothers Inc
3778        Z: Zillow Group (C shares)
175                    AMBA: Ambarella
1258                      EZPW: EZCORP
253                  ARAY: Accuray Inc
967     CY: Cypress Semiconductor Corp
Name: ticker_name, dtype: object
BLFS: Biolife Solutions Inc
487                 BLFS: Biolife Solutions Inc
2849            RIGL: Rigel Pharmaceu

Name: ticker_name, dtype: object
CLMT: Calumet Specialty Products Partners
747     CLMT: Calumet Specialty Products Partners
1040           DO:  Diamond Offshore Drilling Inc
1039                   DNR: Denbury Resources Inc
1041            DO: Diamond Offshore Drilling Inc
482                          BLBD: Blue Bird Corp
2985                       SDRL: Seadrill Limited
3772                    YPF: YPF Sociedad Anónima
3771                    YPF: YPF Sociedad Anonima
2518                           OSB: Norbord, Inc.
2582      PBR: Petroleo Brasileiro S.A.-Petrobras
Name: ticker_name, dtype: object
CLNC: Colony Credit Real Estate, Inc.
748           CLNC: Colony Credit Real Estate, Inc.
2621    PFLT: PennantPark Floating Rate Capital Ltd
2459    OCSL: Oaktree Specialty Lending Corporation
686                   CFR: Cullen/Frost Bankers Inc
2684       PNNT: PennantPark Investment Corporation
31      ABTX: Aqua Bounty Technologies Inc. (Reg S)
3802                              ZUO: Zuo

Name: ticker_name, dtype: object
DCOM: Dime Community Bancshares
992           DCOM: Dime Community Bancshares
1300               FFWM: First Foundation Inc
3702                       WSBC: Wesbanco Inc
3578             VLY: Valley National Bancorp
2696        PPBI: Pacific Premier Bancorp Inc
1588                 HBMD: Howard Bancorp Inc
1312         FISI: Financial Institutions Inc
422                  BDGE: Bridge Bancorp Inc
3629           WASH: Washington Trust Bancorp
1307    FIBK: First Interstate Bancsystem Inc
Name: ticker_name, dtype: object
DCPH: Deciphera Pharmaceuticals, Inc.
2770                    QGEN: Qiagen N.V.
100       AGIO: Agios Pharmaceuticals Inc
2537            OYST: Oyster Point Pharma
592     CALA: Calithera Biosciences, Inc.
2115         MCRB: Seres Therapeutics Inc
1548          GTHX: G1 Therapeutics, Inc.
3448                TXG: 10x Genomics Inc
1738            IGMS: IGM Biosciences Inc
2156                MGNX: Macrogenics Inc
3741                     X

...

Name: ticker_name, dtype: object
PLXS: Plexus Corp
2677              PLXS: Plexus Corp
3391        TRS: TriMas Corporation
1734                 IEX: IDEX Corp
2189                     MMM: 3M Co
3390               TRS: TriMas Corp
1326                 FLOW: SPX FLOW
1841    JBT: John Bean Technologies
2312             NDSN: Nordson Corp
2377              NOVT: Novanta Inc
1733                 IEX: IDEX CORP
Name: ticker_name, dtype: object
PLYA: Playa Hotels & Resorts N.V.
2678        PLYA: Playa Hotels & Resorts N.V.
1634           HLT: Hilton Worldwide Holdings
2094    MAR: Marriott International Inc (New)
3742          XHR: Xenia Hotels & Resorts Inc
3205                      SUZ: SUZANO S A/ADR
2858                   RLJ: RLJ Lodging Trust
3207                         SUZ: Suzano S.A.
703      CHH: Choice Hotels International Inc
461       BHR: Braemar Hotels & Resorts, Inc.
2605             PEB: Pebblebrook Hotel Trust
Name: ticker_name, dtype: object
PM: PHILIP MORRIS INTERNATION

2927     SAFE: Safety, Income and Growth, Inc.
1789               INVH: Invitation Homes Inc.
543            BRX: Brixmor Property Group Inc
2087                          MAC: Macerich Co
1900                    KIM: Kimco Realty Corp
2891                           RPT: RPT Realty
147                  ALEX: Alexander & Baldwin
3053    SKT: Tanger Factory Outlet Centers Inc
918                          CTRN: Citi Trends
1864                JOUT: Johnson Outdoors Inc
Name: ticker_name, dtype: object
SAFM: Sanderson Farms Inc
2928                  SAFM: Sanderson Farms Inc
2837          RGA: Reinsurance Group of America
948     CVTI: Covenant Transportation Group Inc
3519           USX: U.S. Xpress Enterprises Inc
780                     CNA: CNA Financial Corp
436                     BEN: Franklin Resources
437                BEN: Franklin Resources Inc.
496                         BMA: Banco Macro SA
2051                      LSTR: Landstar System
700                  CHEF: The Chefs' W

3169                 STG: Sunlands Online Education Group
979                                     DAO: Youdao, Inc.
2491    ONE: OneSmart International Education Group Li...
1545                                GSX: GSX Techedu Inc.
2821                      REDU: RISE Education Cayman Ltd
434       BEDU: Bright Scholar Education Holdings Limited
1108             EDU: New Oriental Education & Tech Group
1263                                    FANH: Fanhua Inc.
1109    EDU: New Oriental Education & Technology Group...
3246                             TAL: TAL Education Group
Name: ticker_name, dtype: object
STI: SunTrust Banks
3170                   STI: SunTrust Banks
2495                        OPB: Opus Bank
3074            SMBK: SmartFinancial, Inc.
2331    NEWT: NEWTEK BUSINESS SERVICES COR
2801           RBNC: Reliant Bancorp, Inc.
1413             GBCI: Glacier Bancorp Inc
684       CFB: CrossFirst Bankshares, Inc.
1365      FRBK: Republic First Bancorp Inc
1086             DYNC: 

Name: ticker_name, dtype: object
TSN: Tyson Foods Inc
3412                    TSN: Tyson Foods Inc
1093          EAT: Brinker International Inc
2310                     NDLS: Noodles & Co.
2896    RRGB: Red Robin Gourmet Burgers Inc.
3244        TACO: Del Taco Restaurants, Inc.
1536                       GRUB: GrubHub Inc
3243         TACO: Del Taco Restaurants Inc.
2106                    MCD: McDonald's Corp
2914      RUTH: Ruth's Hospitality Group Inc
772          CMG: Chipotle Mexican Grill Inc
Name: ticker_name, dtype: object
TSS: Total System Services Inc
3413    TSS: Total System Services Inc
298                 ATEN: A10 Networks
2404               NTNX: Nutanix, Inc.
2227         MRCY: Mercury Systems Inc
2559    PANW: Palo Alto Networks, Inc.
2675                   PLUS: ePlus Inc
925           CTXS: Citrix Systems Inc
3482                  UIS: Unisys Corp
2378                  NOW: Service Now
2399        NTCT: Netscout Systems Inc
Name: ticker_name, dtype: object
TSU: Tim 

2103                MBUU: Malibu Boats Inc
2082    LYV: Live Nation Entertainment Inc
3331                TJX: The TJX Companies
3332          TJX: The TJX Companies, Inc.
3330             TJX: TJX Companies, Inc. 
923        CTT: CatchMark Timber Trust Inc
1316                  FIVE: Five Below Inc
1141                    ELY: Callaway Golf
2108               MCFT: MCBC Holdings Inc
2616              PETS: PetMed Express Inc
Name: ticker_name, dtype: object
WFC: Wells Fargo & Co
3511                          USB: US Bancorp
3657                    WFC: Wells Fargo & Co
579                 CAC: Camden National Corp
2519             OSBC: Old Second Bancorp Inc
3174                    STL: Sterling Bancorp
3464    UCFC: United Community Financial Corp
2617                     PFBC: Preferred Bank
1719             IBTX: Independent Bank Group
3712                 WTFC: Wintrust Financial
354                    AX: Axos Financial Inc
Name: ticker_name, dtype: object
WGO: Winnebago Industr

In [19]:
peers_lda.loc[peers_lda.company.str.contains('AMZN'),]

company                                peer     value
59    AMZN: Amazon.com Inc                 ADI: Analog Devices  0.998127
182   AMZN: Amazon.com Inc         AMD: Advanced Micro Devices  0.973352
207   AMZN: Amazon.com Inc                AMZN: Amazon.com Inc  0.999993
322   AMZN: Amazon.com Inc                AUDC: Audiocodes Ltd  0.984023
661   AMZN: Amazon.com Inc    CDNS: Cadence Design Systems Inc  0.985758
1378  AMZN: Amazon.com Inc                        FSLY: FASTLY  0.995818
1784  AMZN: Amazon.com Inc                    INTC: Intel Corp  0.989903
2089  AMZN: Amazon.com Inc             MAN: ManpowerGroup Inc.  0.964537
2221  AMZN: Amazon.com Inc  MPWR: Monolithic Power Systems Inc  0.954711
2420  AMZN: Amazon.com Inc                        NVDA: Nvidia  0.994374
2551  AMZN: Amazon.com Inc          PAH: Element Solutions Inc  0.970446
3095  AMZN: Amazon.com Inc                  SNPS: Synopsys Inc  0.956459
3117  AMZN: Amazon.com Inc                    SPLK: Splunk Inc  0.985828
3118  AMZN: Amazon.com Inc                   SPLK: Splunk Inc.  0.990527
3744  AMZN: Amazon.com Inc                    XLNX: Xilinx Inc  0.972779